# **Google drive Mounting**

In [1]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
!pip install transformers
!pip install huggingface_hub

In [ ]:
from huggingface_hub import notebook_login
notebook_login()

In [ ]:
model.save_pretrained("https://huggingface.co/FuluM21/AfriBert/tree/main")
tokenizer.save_pretrained("https://huggingface.co/FuluM21/AfriBert/")

NameError: name 'model' is not defined

# **Loading data**

In [2]:
import os
from bs4 import BeautifulSoup

data_folder = '/content/drive/My Drive/Data/HUISGENOOT/'

number_files = 0

corpus = ""
for filename in os.listdir(data_folder):
    if filename.endswith(".html"):
        number_files = number_files + 1
        with open(os.path.join(data_folder, filename), 'r', encoding='utf-8') as file:
            html_content = file.read()
            soup = BeautifulSoup(html_content, 'html.parser')
            text = soup.get_text()
            corpus += text + "\n"

    if number_files == 10:
        break

# Saving the preprocessed text to a file
with open('/content/drive/My Drive/Data/HUISGENOOT_corpus_v5.txt', 'w', encoding='utf-8') as file:
    file.write(corpus)


# **Data Cleaning**

In [3]:
import re

def clean_text(text):
    # Remove newlines, extra spaces, and non-breaking spaces
    text = text.replace('\n', ' ').replace('\xa0', ' ').strip()

    # Remove special characters and numbers using regex
    text = re.sub(r'[^a-zA-Z\s]', '', text)

    # Convert multiple spaces into single space
    text = re.sub(r'\s+', ' ', text)

    return text.lower()  # Convert text to lowercase

# Apply cleaning function to your corpus
cleaned_corpus = clean_text(corpus)

# **Data Tokenization**

In [4]:
import nltk
nltk.download('punkt')
nltk.download('stopwords')
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [5]:
import nltk
nltk.data.path.append("'/content/drive/My Drive/Data/Stopw")

In [6]:
# Defining Afrikaans stop words
afrikaans_stop_words = set(stopwords.words('dutch'))

# Tokenize text
tokens = word_tokenize(cleaned_corpus)

# Remove stop words
filtered_tokens = [word for word in tokens if word.lower() not in afrikaans_stop_words]

# Join tokens back into a single string
filtered_text = ' '.join(filtered_tokens)

# Save the preprocessed text to a file
with open('/content/drive/My Drive/Data/HUISGENOOT_corpus_preprocessed.txt', 'w', encoding='utf-8') as file:
    file.write(filtered_text)


# **Training**

In [7]:
!pip install transformers[torch]
!pip install accelerate>=0.21.0 --upgrade

from transformers import GPT2Tokenizer, GPT2LMHeadModel
from transformers import TextDataset, DataCollatorForLanguageModeling
from transformers import Trainer, TrainingArguments

# Load the tokenizer
tokenizer = GPT2Tokenizer.from_pretrained("gpt2")

# Tokenize the dataset
train_path = '/content/drive/My Drive/Data/HUISGENOOT_corpus_v5.txt'
train_dataset = TextDataset(
    tokenizer=tokenizer,
    file_path=train_path,
    block_size=128
)

# Create data collator
data_collator = DataCollatorForLanguageModeling(
    tokenizer=tokenizer, mlm=False
)

# Initialize the model
model = GPT2LMHeadModel.from_pretrained("gpt2")

# Define the training arguments
training_args = TrainingArguments(
    output_dir="./gpt2-afrikaans",
    overwrite_output_dir=True,
    num_train_epochs=3,
    per_device_train_batch_size=4,
    save_steps=10_000,
    save_total_limit=2,
    prediction_loss_only=True,
)

# Create Trainer instance
trainer = Trainer(
    model=model,
    args=training_args,
    data_collator=data_collator,
    train_dataset=train_dataset,
)

# Start training
trainer.train()


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/transformers/data/datasets/language_modeling.py:53:

TrainOutput(global_step=225, training_loss=4.451516384548611, metrics={'train_runtime': 2131.93, 'train_samples_per_second': 0.418, 'train_steps_per_second': 0.106, 'total_flos': 58202800128000.0, 'train_loss': 4.451516384548611, 'epoch': 3.0})

In [ ]:
!pip install --upgrade accelerate
exit() # Restart the kernel after running this cell

# **Model Saving**

In [8]:
# Save the trained model
output_dir = "./gpt2-afrikaans"
model.save_pretrained(output_dir)
tokenizer.save_pretrained(output_dir)

('./gpt2-afrikaans/tokenizer_config.json',
 './gpt2-afrikaans/special_tokens_map.json',
 './gpt2-afrikaans/vocab.json',
 './gpt2-afrikaans/merges.txt',
 './gpt2-afrikaans/added_tokens.json')

# **Trained data Calling (11-50)**

In [9]:
# Load the preprocessed text from article 11-50
with open('/content/drive/My Drive/Data/HUISGENOOT_corpus_11_50.txt', 'r', encoding='utf-8') as file:
    corpus_51_550 = file.read()

#Trained data Calling (51-550)

In [10]:
# Load the preprocessed text from article 51-550
with open('/content/drive/My Drive/Data/HUISGENOOT_corpus_51_550.txt', 'r', encoding='utf-8') as file:
    corpus_51_550 = file.read()

# Trained data calling (551-1000)

In [11]:
# Load the preprocessed text from article 551-1000
with open('/content/drive/My Drive/Data/HUISGENOOT_corpus_551_1000.txt', 'r', encoding='utf-8') as file:
    corpus_551_1000 = file.read()

# **Trained data Calling (1001 - 1800)**

In [12]:
# Load the preprocessed text from article 1001 - 1800
with open('/content/drive/My Drive/Data/HUISGENOOT_corpus_1001_1800.txt', 'r', encoding='utf-8') as file:
    corpus_1001_1800 = file.read()

# **Model Testing**

In [13]:
from transformers import pipeline

# Load the fine-tuned model
model_path = "./gpt2-afrikaans"  # Adjust the path accordingly
tokenizer = GPT2Tokenizer.from_pretrained(model_path)
model = GPT2LMHeadModel.from_pretrained(model_path)

# Set up text generation pipeline
text_generator = pipeline("text-generation", model=model, tokenizer=tokenizer)

# Generate text
prompt = "Ek het 'n droom gehad"
generated_text = text_generator(prompt, max_length=100, num_return_sequences=1)
print(generated_text[0]['generated_text'])

Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Ek het 'n droom gehad in die hoe nie die klange oorstie die skitterklaas, sy het met gedak wat ons uit gekrag te het in die het vrous die beteken vir een eejoon, haar in vir nou koië nie. “Hoy ek die klaas het ek op ’n m


In [ ]:
prompt2 = "Hou oud is jy"
generated_text2 = text_generator(prompt2, max_length=100, num_return_sequences=1)
print(generated_text2[0]['generated_text'])

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Hou oud is jy wêreld.


Daar is jy wat ek voel by die jongbukkakeld met die kommer van my party aan die skaat. Ek is vermorkig by dié raad met die kommunikings van die steeds om om te bordeljies en vermaaan kou, maar gekry in die maou in jou kon n


In [ ]:
prompt3 = "Vertel my van die nuutste berigte in Huisgenoot."
generated_text3 = text_generator(prompt3, max_length=100, num_return_sequences=1)
print(generated_text3[0]['generated_text'])

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Vertel my van die nuutste berigte in Huisgenoot. 


Gwyneth Paltrow (@wiebestsellers) is en laatste maar nou be­der vuil vir my lewe.










REDAACHT


DIE GROOTTE, MELISSA BAKER, GEORGE HANSBURG






LIEVELANDE RUMS


JP


In [ ]:
prompt4 = "Wat is jou gunsteling Huisgenoot artikel en hoekom?"
generated_text4 = text_generator(prompt4, max_length=100, num_return_sequences=1)
print(generated_text4[0]['generated_text'])

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Wat is jou gunsteling Huisgenoot artikel en hoekom?” he moet toe jou gee. (Huisgenoot verstaan van die RUSSIAN PETERS.) 
“Hoe beter Jy uit gehad het van die RUSSIAN PETERS gebore het en word oor die RUSSIAN PETERS wanneer gesê die ook sy het


In [ ]:
prompt5 = "Wat is die naam van die tydskrif?"
generated_text5 = text_generator(prompt5, max_length=100, num_return_sequences=1)
print(generated_text5[0]['generated_text'])

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Wat is die naam van die tydskrif?” vertel nór die gesien het, kon verhouding van die tydskrif vir skryf oor die tydskrif van die die gekom nou in lewe.
Dit was twee die opgemaar tydste tydste boeke opgeveel om een vrou daardie na haar


In [ ]:
prompt6 = "Hoe het Huisgenoot oor belangrike historiese gebeurtenisse in Suid-Afrika berig?"
generated_text6 = text_generator(prompt6, max_length=100, num_return_sequences=1)
print(generated_text6[0]['generated_text'])

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Hoe het Huisgenoot oor belangrike historiese gebeurtenisse in Suid-Afrika berig? 
“Ek geen uit altyd hoe verdoon om by die dae te minstel verhouding hulle geleur ’n oor julle bly die diefe oor die jou van die bly.” 
Ek kan altyd


# **Downstream Applications**

In [14]:
from transformers import AutoTokenizer, AutoModelForQuestionAnswering

# Replace 'your-pretrained-model-name' with the actual name of the model
model_name = "bert-base-uncased" # Example: using a public model
tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForQuestionAnswering.from_pretrained(model_name)

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(
Some weights of BertForQuestionAnswering were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['qa_outputs.bias', 'qa_outputs.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
!pip uninstall -y pyarrow
!pip install pyarrow

Found existing installation: pyarrow 14.0.2
Uninstalling pyarrow-14.0.2:
  Successfully uninstalled pyarrow-14.0.2
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 20.4 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf-cu12 24.4.1 requires pyarrow<15.0.0a0,>=14.0.1, but you have pyarrow 17.0.0 which is incompatible.
ibis-framework 8.0.0 requires pyarrow<16,>=2, but you have pyarrow 17.0.0 which is incompatible.


In [15]:
from datasets import load_dataset

dataset = load_dataset("squad")


README.md:   0%|          | 0.00/7.62k [00:00<?, ?B/s]

train-00000-of-00001.parquet:   0%|          | 0.00/14.5M [00:00<?, ?B/s]

validation-00000-of-00001.parquet:   0%|          | 0.00/1.82M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/87599 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/10570 [00:00<?, ? examples/s]

In [15]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 474.3/474.3 kB 14.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 7.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 19.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 9.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 12.5 MB/s eta 0:00:00
  Attempting uninstall: pyarrow
    Found existing installation: pyarrow 14.0.2
    Uninstalling pyarrow-14.0.2:
      Successfully uninstalled pyarrow-14.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf-cu12 24.4.1 requires pyarrow<15.0.0a0,>=14.0.1, but you have pyarrow 17.0.0 which is incompatible.
ibis-framework 8.0.0 requires pyarrow<16,>=2, but you have pyarrow 17.0.0 which is incompatible.


In [16]:
def preprocess_function(examples):
    questions = [q.strip() for q in examples["question"]]
    inputs = tokenizer(
        questions,
        examples["context"],
        max_length=384,
        truncation="only_second",
        return_offsets_mapping=True,
        padding="max_length",
    )

    offset_mapping = inputs.pop("offset_mapping")
    answers = examples["answers"]
    start_positions = []
    end_positions = []

    for i, offset in enumerate(offset_mapping):
        answer = answers[i]
        start_char = answer["answer_start"][0]
        end_char = start_char + len(answer["text"][0])
        sequence_ids = inputs.sequence_ids(i)

        context_start = sequence_ids.index(1)
        context_end = len(sequence_ids) - 1 - sequence_ids[::-1].index(1)

        if offset[context_start][0] > end_char or offset[context_end][1] < start_char:
            start_positions.append(0)
            end_positions.append(0)
        else:
            # Find the start and end positions using the offset mapping
            start_position = end_position = 0  # Initialize to 0
            for j, (s, e) in enumerate(offset):
                if s == start_char:
                    start_position = j
                if e == end_char:
                    end_position = j
                    break

            start_positions.append(start_position) # Append the found position or 0
            end_positions.append(end_position)   # Append the found position or 0

    inputs["start_positions"] = start_positions
    inputs["end_positions"] = end_positions
    return inputs

tokenized_datasets = dataset.map(preprocess_function, batched=True)

Map:   0%|          | 0/87599 [00:00<?, ? examples/s]

Map:   0%|          | 0/10570 [00:00<?, ? examples/s]

In [ ]:
from transformers import TrainingArguments, Trainer

training_args = TrainingArguments(
    output_dir="./results",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_datasets["train"],
    eval_dataset=tokenized_datasets["validation"],
)

trainer.train()

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [ ]:
results = trainer.evaluate()
print(results)